In [1]:
# basic imports
import pandas as pd
import numpy as np
import os

# image manipulation
from PIL import Image

#yolov8
import ultralytics
from ultralytics import YOLO

#roboflow
from roboflow import Roboflow

In [2]:
#function to pad image to a square shape: 
def expand2square(pill_img, background_color):
    width, height = pill_img.size
    if width == height:
        return pill_img
    elif width > height:
        result = Image.new(pill_img.mode, (width, width), background_color)
        result.paste(pill_img, (0, (width - height) // 2))
        return result
    else:
        result = Image.new(pill_img.mode, (height, height), background_color)
        result.paste(pill_img, ((height - width) // 2, 0))
        return result

In [3]:
pill_list = ['advil', 'advil_liqui-gel', 'advil_400', 'kirkland_acetaminophen', 'life_acetaminophen']

model_dir = os.path.join(os.path.expanduser("~"), "Downloads", "best.pt")
images_dir = os.path.join(os.path.expanduser("~"), "Downloads", "pill_vids")
output_images_dir = os.path.join(os.path.expanduser("~"), "Downloads", "pill_vids_output")

model = YOLO(model_dir)

for pill_name in pill_list:

  # Cleaning subdirectories with the different pills
  input_images_pill_dir = os.path.join(images_dir, pill_name) # directory with input images
  output_images_pill_dir = os.path.join(output_images_dir, pill_name) # directory with output images
  
  #creates output pill folder if it does not exist
  if os.path.exists(output_images_pill_dir) == False:
    os.mkdir(output_images_pill_dir) # output directory

  for image_name in os.listdir(input_images_pill_dir):
    input_image_path = os.path.join(input_images_pill_dir, image_name)

    if image_name.endswith('cr2'): #ensures input format is not cr2 (canon)
      continue
  
    #if image_name.endswith('wmv'): #ensures input format is not video
      #continue
      
    # Running predictions 
    results = model.predict(input_image_path, conf=0.4, overlap_mask=True, save_crop=True) 

    if os.path.exists('runs/detect/predict/crops/pill') == False: # yolo has not detected any pill in the image
      continue
    
    for cropped_image_name in os.listdir('runs/detect/predict/crops/pill'):
    
      cropped_image_path = os.path.join('runs/detect/predict/crops/pill', cropped_image_name)
      cropped_image = Image.open(cropped_image_path)
      preprocessed_image=expand2square(cropped_image, (0, 0, 0)) # Extending with zeros
      preprocessed_image=preprocessed_image.resize((160, 160)) # Resizing to 160 x 160 (defaut is 640x640 for yolo)
      preprocessed_image.save(os.path.join(output_images_pill_dir, str(cropped_image_name)), format='JPEG', subsampling=0, quality=95)

    #removing runs directory 
    !rm -r 'runs'



    WARNING ⚠️ stream/video/webcam/dir predict source will accumulate results in RAM unless `stream=True` is passed,
    causing potential out-of-memory errors for large sources or long-running streams/videos.

    Usage:
        results = model(source=..., stream=True)  # generator of Results objects
        for r in results:
            boxes = r.boxes  # Boxes object for bbox outputs
            masks = r.masks  # Masks object for segment masks outputs
            probs = r.probs  # Class probabilities for classification outputs

video 1/1 (1/551) /Users/ninaadkalla/Downloads/pill_vids/advil/IMG_6140.MOV: 384x640 1 Pill, 67.3ms
video 1/1 (2/551) /Users/ninaadkalla/Downloads/pill_vids/advil/IMG_6140.MOV: 384x640 1 Pill, 58.9ms
video 1/1 (3/551) /Users/ninaadkalla/Downloads/pill_vids/advil/IMG_6140.MOV: 384x640 1 Pill, 60.7ms
video 1/1 (4/551) /Users/ninaadkalla/Downloads/pill_vids/advil/IMG_6140.MOV: 384x640 1 Pill, 66.5ms
video 1/1 (5/551) /Users/ninaadkalla/Downloads/pill_vids/ad